In [4]:
# Работа с табличными данными

import pandas as pd
import numpy as np


# Визуализация

import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_dark'
from motorica.emg8.utils import fig_montage # кастомная функия визуализации


# Пайплайн

# чтение данных и разметка по фактическим жестам
from motorica.emg8.pipeline import read_emg8
# создание экземпляра пайплайна на базе логистической регрессии      
from motorica.emg8.pipeline import create_logreg_pipeline
# константы
from motorica.emg8.pipeline import OMG_CH, CMD_COL, STATE_COL, TARGET


# Метрики
from sklearn.metrics import classification_report


# Для вывода докстрингов с форматированием markdown
from IPython.display import Markdown as md

# Работа с файлами
import os

# Для оценки скорости инференса
from time import time

## Подгрузка и разметка данных

Список имеющихся файлов с данными:

In [5]:
# Папка с файлами данных
DATA_DIR = 'data/new'

montages = sorted(filter(lambda f: f.endswith('.emg8'), os.listdir(DATA_DIR)))
montages

['2024-12-02_14-03-05.emg8',
 '2024-12-04_12-22-13.emg8',
 '2024-12-09_11-22-43.emg8']

In [6]:
montage = montages[-1]
gestures_raw = pd.read_csv(os.path.join(DATA_DIR, montage), sep=' ')
fig_montage(
    gestures_raw[OMG_CH], y_cmd=gestures_raw['id'], 
    title=f"<i>{montage}</i> – исходные данные"
).show()

В качестве отложенной выборки оставим последний цикл протокола:

In [7]:
LAST_TRAIN_IDX = 4550

X_train, X_test, y_train, y_test, gestures = read_emg8(montage, last_train_idx=LAST_TRAIN_IDX)

print('X_train shape:', X_train.shape)
print('y_train shape:', y_train.shape)
print('X_test shape:', X_test.shape)
print('y_test shape:', y_test.shape)

state_id = gestures[['id', 'state']].drop_duplicates()
GESTURES = state_id['state'] + ' ' + state_id['id'].astype(str)
display(GESTURES)


fig_montage(
    gestures[OMG_CH], y_cmd = gestures[CMD_COL], y_act = gestures[TARGET],
    title=f"<i>{montage}</i> – разметка по фактическим границам жестов"
).show()

X_train shape: (4426, 16)
y_train shape: (4426,)
X_test shape: (1074, 16)
y_test shape: (1074,)


125          Neutral 0
225     ThumbFingers 1
375            Close 2
525             Open 3
675            Pinch 4
825       Indication 5
975       Wrist_Flex 6
1125    Wrist_Extend 7
dtype: object

## Пайплайн

In [8]:
logreg_pl = create_logreg_pipeline(optimize_and_fit=True, X=X_train, y=y_train)
logreg_pl

  0%|          | 0/100 [00:00<?, ?it/s]

Pipeline(steps=[('noise_reduct', NoiseReduction(n_lags=1)),
                ('add_diff', AddDifference(n_lags=2)),
                ('scaler', MinMaxScaler()),
                ('model',
                 PostprocWrapper(estimator=LogisticRegression(C=2,
                                                              max_iter=5000)))])

In [9]:
y_train_pred = logreg_pl.predict(X_train)
y_test_pred = logreg_pl.predict(X_test)

print("Train data " + '-' * 44)
print(classification_report(y_train, y_train_pred, target_names=GESTURES))
print()
print("Test data " + '-' * 45)
print(classification_report(y_test, y_test_pred, target_names=GESTURES))

Train data --------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.94      0.96      0.95      3157
ThumbFingers 1       0.91      0.89      0.90       187
       Close 2       0.89      0.87      0.88       173
        Open 3       0.91      0.90      0.90       193
       Pinch 4       0.88      0.67      0.76       182
  Indication 5       0.90      0.89      0.89       176
  Wrist_Flex 6       0.89      0.86      0.87       173
Wrist_Extend 7       0.91      0.91      0.91       185

      accuracy                           0.93      4426
     macro avg       0.90      0.87      0.88      4426
  weighted avg       0.93      0.93      0.93      4426


Test data ---------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.92      0.97      0.94       753
ThumbFingers 1       1.00      0.15      0.26        46
       Close 2       0.95      0.91      0.

## Симуляция инференса в реальном времени на отложенной выборке

In [10]:
y_test_pred = np.empty(0)
comp_durations = np.empty(0)

for i in range(X_test.shape[0]):
    start_time = time()
    y_test_pred = np.append(y_test_pred, logreg_pl.predict(X_test[i]))
    comp_duration = time() - start_time
    comp_durations = np.append(comp_durations, comp_duration)

print(f"Максимальное время: {np.round(comp_durations.max() * 1000, 2)} мс")
print(f"Среднее время: {np.round(comp_durations.mean() * 1000, 2)} мс")

fig = px.scatter(
    comp_durations * 1000, color=y_test_pred, width=1200, height=500,
    title='Время инференса при последовательных предсказаниях примеров тестовой выборки',
    labels={'value': 'время, мс'}
)
fig.update_coloraxes(showscale=False)
fig.show()

print(classification_report(y_test, y_test_pred, target_names=GESTURES))

fig = fig_montage(
    pd.DataFrame(X_test), 
    y_cmd=gestures.loc[LAST_TRAIN_IDX + 1:, CMD_COL].reset_index(drop=True), 
    y_true=y_test, y_pred=y_test_pred,
    title="Результаты последовательных предсказаний примеров тестовой выборки"
)
fig.show()

Максимальное время: 0.53 мс
Среднее время: 0.26 мс


                precision    recall  f1-score   support

     Neutral 0       0.92      0.97      0.94       753
ThumbFingers 1       1.00      0.15      0.26        46
       Close 2       0.95      0.91      0.93        45
        Open 3       0.92      0.90      0.91        50
       Pinch 4       0.89      0.91      0.90        45
  Indication 5       0.93      0.89      0.91        46
  Wrist_Flex 6       0.90      0.90      0.90        42
Wrist_Extend 7       0.91      0.91      0.91        47

      accuracy                           0.92      1074
     macro avg       0.93      0.82      0.84      1074
  weighted avg       0.92      0.92      0.91      1074

